In [1]:
import load
from plot import plot3D

# from mygp import mygp

import numpy as np
import pandas as pd
from sklearn.gaussian_process import GaussianProcessRegressor
from sklearn.gaussian_process import kernels
from sklearn.preprocessing import StandardScaler

import skopt 
from skopt.space import Real

from icecream import ic




In [2]:
class mygp(object):

    def __init__(
        self,  
        gp=None,  
        **kwargs    
    ):
    
        if gp:
            self.gp = gp    
        else:
            self.gp = GaussianProcessRegressor()    



        self.ndims=1
        self.sample_X = np.array([])
        self.sample_y = np.array([])

        
        self.kwargs = kwargs
        self.kappa = kwargs.pop("kappa",0.0)
        self.acquisition_function = kwargs.pop("acquisition_function","LCB")    
        self.xi = kwargs.pop("xi", 0.01)     


    def prn(self, **kwargs):


        print(f"ndims = {self.ndims}. sample shape = {self.sample_X.shape}")
        ic(self.sample_X, self.sample_y)
        print(f"kappa={self.kappa}")
        print(f"xi={self.xi}")
        print(f"acquisition_function={self.acquisition_function}")    

        return

    def sample_init(self,X,y):

        X_shape = X.shape
        X_len =  len(X_shape)

        
        if X_len == 1:
            self.ndims = 1
        elif X_len == 2:
            self.ndims = X_shape[1]
        else:         
            raise ValueError(f'sample_init() sample_X has incompatiple shape"{X_shape}" for the gaussian fit method.')
        
        self.sample_X = X.copy()
        self.sample_y = y.copy()


        self.gp.fit(self.sample_X, self.sample_y)

        sample_pred , sample_std = self.gp.predict(self.sample_X, return_std=True)

        return sample_pred

    def predict(self, grid_X):
                           
        X_len = len(grid_X.shape)

        if X_len == 1 and self.ndims == 1:
            pass      
        elif X_len ==2 and grid_X.shape[1] == self.ndims:       
            pass        
        else:
            raise ValueError(f'predict() grid_X has shape "{grid_X.shape}" dimensions. ndims = {self.ndims}')   

        grid_pred, grid_std = self.gp.predict(grid_X, return_std=True)

        return grid_pred, grid_std

    def log_marginal_likelihood(self, theta=None,eval_gradient=False, clone_kernel=True):

        return self.gp.log_marginal_likelihood( theta=theta, eval_gradient=eval_gradient,clone_kernel=clone_kernel  )
    
    def get_params(self):
        ic(self.gp.get_params(deep=True))

    def sample_add(self, X1, y1):

        if len(X1) != self.ndims: 
            raise ValueError(f'sample_add(). Error sample_X1 must have exactly "{self.ndims}"')      

        # add point to array
        X = np.concatenate((self.sample_X, [X1]),axis=0 )
        y = np.concatenate((self.sample_y, [y1]),axis=0)     

        # ic(X.shape,y.shape)
        # ic(X,y)
        
        # remember if sucessfull this will update self.sample_X, self.sample_y
        self.sample_init(X,y)

        return
    
    def gp_minimize(self):

        def surrogate_function(inputs):
            # Predict using the Gaussian Process surrogate model
            y_pred, stdev = self.gp.predict(np.atleast_2d(inputs), return_std=True) 
            return y_pred[0]  



        my_domain = [Real(0.0, 1.0, name=f'num_{self.ndims}') for i in range(self.ndims)]    
        
        res = skopt.gp_minimize(
            func=surrogate_function,
            dimensions=my_domain,  # The search space
            # base_estimator= self.gp, 
            acq_func=self.acquisition_function,
            kappa= self.kappa,
            n_calls = 4,  # high to be on the safe side
            
            x0=[list(x) for x in self.sample_X], # Sample X values
            y0= self.sample_y,                   # y target 
            verbose=False                         # debug output ??
        )
        
        print(f"gp_minimize() res.x = {res.x}")
        print(f"gp_minimize() res.fun = {res.fun}")

        suggested = np.array(res.x_iters[-1])
        print("Suggested next inputs to try:", suggested)

        del res  

        return

    def op_minimize(self,X, base_estimator  ):

        if X is None:
            X=np.array([])
         
        values = np.array([])
        my_domain = [Real(0.0, 1.0, name=f'num_{self.ndims}') for i in range(self.ndims)]    

            
        # if self.acquisition_function == "LCB":
        #     acq_func_kwargs = {"kappa": self.kappa}
        # elif self.acquisition_function == "EI" or   self.acquisition_function == "PI":
        #     acq_func_kwargs = {"xi": self.xi}
 
        acq_func_kwargs = {"xi": self.xi, "kappa": self.kappa}      
          
        opt = skopt.Optimizer(
            my_domain,
            base_estimator= self.gp  if base_estimator==None else base_estimator,
            acq_func=self.acquisition_function,
            n_initial_points=1,   
            random_state=0,
            acq_func_kwargs=acq_func_kwargs,
            acq_optimizer='sampling' 
        )
        
        opt.tell(self.sample_X.tolist()   , self.sample_y.tolist(), fit=True)
        possibles = opt.ask()

        # remember opt.models[0] is the base_optimizer in opt
        
        ic(opt.models[0])
        if len(X)>0:
            match self.acquisition_function:
                case "LCB":    
                    values = skopt.acquisition.gaussian_lcb(X, opt.models[0], kappa=self.kappa )    
                case "EI": 
                    values = skopt.acquisition.gaussian_ei(X, opt.models[0], y_opt=np.min(self.sample_y), xi=self.xi )
                case "PI":
                    values = skopt.acquisition.gaussian_pi(X, opt.models[0], y_opt=np.min(self.sample_y), xi=self.xi )    
                case _:
                    raise ValueError(f"op_minimize() unknown acquisition function {self.acquisition_function}") 


        
        # print(f"op_minimize(): value = {values}")         
        # print(f"opt.ask()={possibles}")

        del opt

        return values, possibles
  



a,b = load_function( 1,2 )
ic(a.shape,b.shape)
ic(a,b)


Function_1

In [7]:
x1, x2 = np.meshgrid(np.linspace( 0.0, 1.0, 100), np.linspace(0.0, 1.0, 100))
X_plot = np.vstack([x1.ravel(), x2.ravel()]).T

# kernel = kernels.RBF(length_scale=0.08)
# kernel = kernels.Matern(length_scale=[1, 1], length_scale_bounds=(1e-6, 10)) + kernels.WhiteKernel(noise_level=0.0001)
kernel = kernels.Matern(nu=2.5, length_scale=0.08 )


g = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)


gp = mygp(g, kappa=1.0, acquisition_function="LCB", xi=0.01 )


sample_X, sample_y = load.load_function(1,4)

# sample_y*=-1.0

gp.sample_init(sample_X,sample_y)

gp.prn()

# gp.get_params()
X = np.array([0.5])
y_pred, possibles = gp.op_minimize(X_plot, None)

ic(possibles)


del gp,g


/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/sklearn/gaussian_process/_gpr.py:616: ConvergenceWarning: lbfgs failed to converge (status=2):
ABNORMAL_TERMINATION_IN_LNSRCH.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  _check_optimize_result("lbfgs", opt_res)
ic| self.sample_X: array([[0.31940389, 0.76295937],
                          [0.57432921, 0.8798981 ],
                          [0.73102363, 0.73299988],
                          [0.84035342, 0.26473161],
                          [0.65011406, 0.68152635],
                          [0.41043714, 0.1475543 ],
                          [0.31269116, 0.07872278],
                          [0.68341817, 0.86105746],
                          [0.08250725, 0.40348751],
                          [0.88388983, 0.58225397],
                          [0.651     , 0.68      ],
                          [0.651     , 0.67      ],
         

ndims = 2. sample shape = (13, 2)
kappa=1.0
xi=0.01
acquisition_function=LCB


ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.08, nu=2.5),
                                            n_restarts_optimizer=10)
ic| possibles: [0.001469006142370222, 0.9976027499916044]


In [4]:

y_pred = y_pred.reshape(x1.shape)
ic(x1.shape,x2.shape,y_pred.shape)
ic(np.min(y_pred),np.max(y_pred), np.argmin(y_pred, keepdims=True)  )
plot3D(x1,x2,y_pred)



ic| x1.shape: (100, 100)
    x2

.shape: (100, 100)
    y_pred.shape: (100, 100)
ic| np.min(y_pred): -0.3615865811272165
    np.max(y_pred): 0.03008550534440735
    np.argmin(y_pred, keepdims=True): array([[9900]])
/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/IPython/core/display.py:431: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


[0.2719114490429178, 0.5022348873405836]

GP == ic| opt.models[0]: GaussianProcessRegressor(kernel=1**2 * Matern(length_scale=[1, 1], nu=2.5) + WhiteKernel(noise_level=1), n_restarts_optimizer=2, noise='gaussian', normalize_y=True, random_state=209652396)



function_2

In [28]:
x1, x2 = np.meshgrid(np.linspace( 0.0, 1.0, 100), np.linspace(0.0, 1.0, 100))
X_plot = np.vstack([x1.ravel(), x2.ravel()]).T



kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g2 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp2 = mygp(g2, kappa=1, acquisition_function="EI",xi=0.1 )

# load.print_for_capstone()


sample_X, sample_y = load.load_function(2,3)

# sample_y*=-1.0

gp2.sample_init(sample_X,sample_y)

gp2.prn()

# gp.get_params()

values, suggestion2=gp2.op_minimize(X_plot,"GP")

ic(suggestion2)

del g2, gp2

ic| self.sample_X: array([[0.66579958, 0.12396913],
                          [0.87779099, 0.7786275 ],
                          [0.14269907, 0.34900513],
                          [0.84527543, 0.71112027],
                          [0.45464714, 0.29045518],
                          [0.57771284, 0.77197318],
                          [0.43816606, 0.68501826],
                          [0.34174959, 0.02869772],
                          [0.33864816, 0.21386725],
                          [0.70263656, 0.9265642 ],
                          [0.7       , 0.926     ],
                          [0.7       , 0.826     ],
                          [0.5       , 0.5       ]])
    self.sample_y: array([ 0.53899612,  0.42058624, -0.06562362,  0.29399291,  0.21496451,
                           0.02310555,  0.24461934,  0.03874902, -0.01385762,  0.61120522,
                           0.62292463,  0.6022464 ,  0.69541673])


ndims = 2. sample shape = (13, 2)
kappa=1
xi=0.1
acquisition_function=EI


ic| opt.models[0]: GaussianProcessRegressor(kernel=1**2 * Matern(length_scale=[1, 1], nu=2.5) + WhiteKernel(noise_level=1),
                                            n_restarts_optimizer=2, noise='gaussian',
                                            normalize_y=True, random_state=209652396)
ic| suggestion2: [0.3129534571101283, 0.91866661046231]


In [29]:
y_pred = y_pred.reshape(x1.shape)
ic(x1.shape,x2.shape,y_pred.shape)
ic(np.min(y_pred),np.max(y_pred), np.argmin(y_pred, keepdims=True)  )
plot3D(x1,x2,y_pred)


ic| x1.shape: (100, 100)
    x2.shape: (100, 100)
    

y_pred.shape: (100, 100)
ic| np.min(y_pred): -0.36158658712845676
    np.max(y_pred): 0.03008550611866364
    np.argmin(y_pred, keepdims=True): array([[9900]])
/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/IPython/core/display.py:431: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


y_pred = y_pred.reshape(x1.shape)
ic(x1.shape,x2.shape,y_pred.shape)
ic(np.min(y_pred),np.argmin(y_pred, keepdims=True)  )
plot3D(x1,x2,y_pred)


In [31]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g3 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp3 = mygp(g3, kappa=0.5, acquisition_function="EI", xi=0.1 )

# load.print_for_capstone()


sample_X, sample_y = load.load_function(3,3)

sample_y*=-1.0

gp3.sample_init(sample_X,sample_y)

gp3.prn()

# gp.get_params()

values, possibles =gp3.op_minimize(None, None)

ic(possibles)

del g3, gp3

ic| self.sample_X: array([[0.17152521, 0.34391687, 0.2487372 ],
                          [0.24211446, 0.64407427, 0.27243281],
                          [0.53490572, 0.39850092, 0.17338873],
                          [0.49258141, 0.61159319, 0.34017639],
                          [0.13462167, 0.21991724, 0.45820622],
                          [0.34552327, 0.94135983, 0.26936348],
                          [0.15183663, 0.43999062, 0.99088187],
                          [0.64550284, 0.39714294, 0.91977134],
                          [0.74691195, 0.28419631, 0.22629985],
                          [0.17047699, 0.6970324 , 0.14916943],
                          [0.22054934, 0.29782524, 0.34355534],
                          [0.66601366, 0.67198515, 0.2462953 ],
                          [0.04680895, 0.23136024, 0.77061759],
                          [0.60009728, 0.72513573, 0.06608864],
                          [0.96599485, 0.86111969, 0.56682913],
                          [0.493     , 0

ndims = 3. sample shape = (18, 3)
kappa=0.5
xi=0.1
acquisition_function=EI


ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.01, nu=2.5),
                                            n_restarts_optimizer=10)
ic| possibles: [0.4142210500958916, 0.47679831977223863, 0.45518038913779724]


In [ ]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g4 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp4 = mygp(g4, kappa=1.0, acquisition_function="EI", xi=0.1)

# load.print_for_capstone()


sample_X, sample_y = load.load_function(4,3)

gp4.sample_init(sample_X,sample_y)

# gp4.prn()

# gp.get_params()

values, possibles = gp4.op_minimize(None, None)

ic(possibles)

del g4, gp4

/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/sklearn/gaussian_process/_gpr.py:616: ConvergenceWarning: lbfgs failed to converge (status=2):
ABNORMAL_TERMINATION_IN_LNSRCH.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
  _check_optimize_result("lbfgs", opt_res)
ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.01, nu=2.5),
                                            n_restarts_optimizer=10)
ic| possibles: [0.9883738380592264, 0.9059989949325632, 0.829899059222762, 0.5873737506385249]


In [42]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g5 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp5 = mygp(g5, kappa=1.0, acquisition_function="EI", xi=0.1)

# load.print_for_capstone()

ic(sample_y)

sample_X, sample_y = load.load_function(5,3)

gp5.sample_init(sample_X,sample_y)

# gp4.prn()

# gp.get_params()

values, possibles = gp5.op_minimize(None, None)

ic(possibles)

del g5, gp5

ic| sample_y: array([6.44434399e+01, 1.83013796e+01, 1.12939795e-01, 4.21089813e+00,
                     2.58370525e+02, 7.84343889e+01, 5.75715369e+01, 1.09571876e+02,
                     8.84799176e+00, 2.33223610e+02, 2.44230883e+01, 6.44201468e+01,
                     6.34767158e+01, 7.97291299e+01, 3.55806818e+02, 1.08885962e+03,
                     2.88667516e+01, 4.51815703e+01, 4.31612757e+02, 9.97233189e+00,
                     1.09115802e+03, 2.54361332e+02, 9.38784182e+01])
ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.01, nu=2.5),
                                            n_restarts_optimizer=10)
ic| possibles: [0.7277712732144181, 0.667574500517014, 0.36544699719012125, 0.6358746605355162]


In [48]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g6 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp6 = mygp(g6, kappa=1.0, acquisition_function="EI", xi=0.1)

# load.print_for_capstone()

ic(sample_y)

sample_X, sample_y = load.load_function(6,3)

sample_y *= -1.0

gp6.sample_init(sample_X,sample_y)

# gp6.prn()

# gp6.get_params()

values, possibles = gp6.op_minimize(None, None)

ic(possibles)

del g6, gp6

ic| sample_y: array([0.71426495, 1.20995524, 1.67219994, 1.53605771, 0.82923655,
                     1.24704893, 1.23378638, 1.69434344, 2.57116963, 1.30911635,
                     1.14478485, 1.91267714, 1.62283895, 1.35668211, 2.0184254 ,
                     1.70255784, 1.29424696, 0.93575656, 2.15576776, 1.74688209,
                     0.72268519, 0.69746093, 1.15181833])
ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.01, nu=2.5),
                                            n_restarts_optimizer=10)
ic| possibles: [0.2245238664931019,
                0.5923650719845006,
                0.03663195033674938,
                0.9807105485297618,
                0.1600672198474629]


In [52]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g7 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp7 = mygp(g7, kappa=2.0, acquisition_function="LCB", xi=0.1)

# load.print_for_capstone()

ic(sample_y)

sample_X, sample_y = load.load_function(7,3)

sample_y *= -1.0

gp7.sample_init(sample_X,sample_y)

# gp6.prn()

# gp6.get_params()

values, possibles = gp7.op_minimize(None, "GP")

ic(possibles)

del g7, gp7

ic| sample_y: array([

-0.6044327 , -0.56275307, -0.00750324, -0.0614243 , -0.2730468 ,
                     -0.08374657, -1.3649683 , -0.09264495, -0.0178696 , -0.03356494,
                     -0.0735163 , -0.2063097 , -0.00882563, -0.26840032, -0.61152553,
                     -0.01479818, -0.27489251, -0.06676325, -0.04211835, -0.00270147,
                     -0.01820907, -0.00701603, -0.10050661, -0.47539552, -0.67514163,
                     -0.51645722, -0.00377748, -0.00313433, -0.02134252, -0.09541116,
                     -1.35771305, -1.35771305, -0.06987356])
ic| opt.models[0]: GaussianProcessRegressor(kernel=1**2 * Matern(length_scale=[1, 1, 1, 1, 1, 1], nu=2.5) + WhiteKernel(noise_level=1),
                                            n_restarts_optimizer=2, noise='gaussian',
                                            normalize_y=True, random_state=209652396)
ic| possibles: [0.012877261910938968,
                0.7341880622680185,
                0.8202897275605,
                0.07918568219

In [57]:
kernel = kernels.Matern(nu=2.5,length_scale=0.01)

g8 = GaussianProcessRegressor(kernel=kernel,n_restarts_optimizer=10)

gp8 = mygp(g8, kappa=2.0, acquisition_function="EI", xi=0.1)

# load.print_for_capstone()

ic(sample_y)

sample_X, sample_y = load.load_function(8,3)

sample_y *= -1.0

gp8.sample_init(sample_X,sample_y)

# gp6.prn()

# gp6.get_params()

values, possibles = gp8.op_minimize(None, None)

print(possibles)

del g8, gp8

ic| sample_y: array([-7.3987211 , -7.00522736, -8.45948162, -8.28400781, -

8.60611679,
                     -8.54174792, -7.32743458, -7.29987205, -7.95787474, -5.59219339,
                     -7.85454099, -6.79198578, -8.97655402, -7.3790829 , -9.598482  ,
                     -8.15998319, -7.13162397, -6.76796253, -7.43374407, -9.01307515,
                     -7.31089382, -5.84106731, -9.14163949, -8.81755844, -6.45194313,
                     -8.83074505, -9.34427428, -6.88784639, -8.04221254, -7.69236805,
                     -7.92375877, -8.42175924, -8.2780624 , -7.11345716, -6.40258841,
                     -8.47293632, -7.97768459, -7.46087219, -7.43659353, -9.18300525,
                     -9.59862285, -9.52782054, -8.7983    ])
ic| opt.models[0]: GaussianProcessRegressor(kernel=Matern(length_scale=0.01, nu=2.5),
                                            n_restarts_optimizer=10)


[0.13020496221070257, 0.21673747560879691, 0.14895170636719327, 0.1754880807967786, 0.5490802856432188, 0.4423748574983052, 0.28348936343641135, 0.6728204205630476]


[0.5097720333627324, 0.9672957700438277]

In [ ]:
acquisition_function=EI/ np=initial
opt.ask()=[0.5483193378701833, 0.5354368030125956, 0.3552665974223879, 0.3502862221350623]

In [ ]:
x1, x2 = np.meshgrid(np.linspace( 0.0, 1.0, 100), np.linspace(0.0, 1.0, 100))
X_plot = np.vstack([x1.ravel(), x2.ravel()]).T

ic(x1.shape,x2.shape,X_plot.shape)

# Predict on the meshgrid
y_pred, y_std = gp.predict(X_plot)    


ic(np.min(y_pred), np.max(y_pred))
y_pred_plot = y_pred.reshape(x1.shape)
y_std_plot  = y_std.reshape(x1.shape)

ic(y_pred.shape, y_std.shape, y_pred_plot.shape, y_std_plot.shape)

plot3D(x1,x2,y_pred_plot+y_std_plot)
#plot3D(x1,x2,y_std_plot)

ic| x1.shape: (100, 100)
    x2.shape: (100, 100)
    X_plot.

shape: (10000, 2)
ic| np.min(y_pred): -0.48709583434629167
    np.max(y_pred): 0.46658415293404687
ic| y_pred.shape: (10000,)
    y_std.shape: (10000,)
    y_pred_plot.shape: (100, 100)
    y_std_plot.shape: (100, 100)
/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/IPython/core/display.py:431: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


In [65]:


def func_z(X,Y):
    Z = np.sin(  (X-0.4)**2 + (Y-0.6)**2)   -  3.0    
    return Z


In [66]:
X, Y = np.meshgrid(np.linspace(0.0,1.0,100),np.linspace(0.0,1.0, 100))
Z = func_z(X,Y)
plot3D(X,Y,Z)




/home/hmb/anaconda3/envs/ts/lib/python3.10/site-packages/IPython/core/display.py:431: UserWarning: Consider using IPython.display.IFrame instead
  warnings.warn("Consider using IPython.display.IFrame instead")


a,b  = load.load_function(1,3)
ic(a,b)

In [67]:

num_points= 6

X = np.random.uniform(0,1.0,num_points)
Y = np.random.uniform(0,1.0,num_points)

s_y *= -1.0

s_y = func_z(X,Y)
s_X = np.vstack([X.ravel(), Y.ravel()]).T

ic(X,Y, s_X)


k=kernels.Matern(length_scale=0.1)

gs = GaussianProcessRegressor(kernel=k,n_restarts_optimizer=10)

gn = mygp(gs, kappa=3.0, acquisition_function="LCB" )


gn.sample_init(s_X,s_y)

gn.prn()

# gp.get_params()


# for idx in range(0,4):


for idx in range(0,14):
    pred_X = gn.op_minimize()
    pred_y = func_z(pred_X[0], pred_X[1] )
    

    gn.sample_add(pred_X,pred_y)  
   
    ic(pred_y)  





ic| X: array([0.70243128, 0.46133782, 0.32022431, 0.90730816, 0.63466216,
              0.62768486])
    Y: array([0.72269662, 0.710742  , 0.3335684 , 0.08654893, 0.2852084 ,
              0.06728137])
    s_X: array([[0.70243128, 0.72269662],
                [0.46133782, 0.710742  ],
                [0.32022431, 0.3335684 ],
                [0.90730816, 0.08654893],
                [0.63466216, 0.2852084 ],
                [0.62768486, 0.06728137]])
ic| self.sample_X: array([[0.70243128, 0.72269662],
                          [0.46133782, 0.710742  ],
                          [0.32022431, 0.3335684 ],
                          [0.90730816, 0.08654893],
                          [0.63466216, 0.2852084 ],
                          [0.62768486, 0.06728137]])
    self.sample_y: array([-2.89368218, -2.98397457, -2.92272715, -2.50225786, -2.84644981,
                          -2.67063635])
ic| pred_y: -2.6883634180502503


ndims = 2. sample shape = (6, 2)
kappa=3.0
xi=0.01
acquisition_function=LCB
opt.ask()=[0.001469006142370222, 0.9976027499916044]


ic| pred_y: -2.9981536036721943


opt.ask()=[0.38377672793369544, 0.560210518721828]
opt.ask()=[0.4980547701201967, 0.5607803140425098]


ic| pred_y: -2.988847309502944
ic| pred_y: -2.9842395833002717
ic| pred_y: -2.999059878368652


...

opt.ask()=[0.38962282432220463, 0.6010351355728448]
opt.ask()=[0.4128966169083216, 0.6122341283238132]


ic| pred_y: -2.9963615957400016
ic| pred_y: -2.999979360363542


opt.ask()=[0.42848215448923455, 0.5468287750449415]
opt.ask()=[0.40177978929262714, 0.6041799505419705]


ic| pred_y: -2.9995607074819652
ic| pred_y: -2.9999253101496866


opt.ask()=[0.386440679824989, 0.6159824080962566]
opt.ask()=[0.40853527539683443, 0.5986439305759146]


In [2]:
load.print_for_capstone()

0.001469-0.997603-
0.000367-0.005225-
0.414221-0.476798-0.455180-
0.988374-0.905999-0.829899-0.587374-
0.727771-0.667575-0.365447-0.635875-
0.224524-0.592365-0.036632-0.980711-0.160067-
0.012877-0.734188-0.820290-0.079186-0.373439-0.791483-
0.130205-0.216737-0.148952-0.175488-0.549080-0.442375-0.283489-0.672820-
